<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Introduction:-Plotly-Visualizations" data-toc-modified-id="Introduction:-Plotly-Visualizations-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Introduction: Plotly Visualizations</a></span><ul class="toc-item"><li><span><a href="#Load-Comparisons-Data" data-toc-modified-id="Load-Comparisons-Data-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Load Comparisons Data</a></span></li><li><span><a href="#Loading-Data" data-toc-modified-id="Loading-Data-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Loading Data</a></span></li><li><span><a href="#Select-Building" data-toc-modified-id="Select-Building-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Select Building</a></span></li></ul></li><li><span><a href="#Start-Time-Plot" data-toc-modified-id="Start-Time-Plot-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Start Time Plot</a></span></li><li><span><a href="#Conclusions" data-toc-modified-id="Conclusions-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Conclusions</a></span></li></ul></div>

# Introduction: Plotly Visualizations

In this notebook, we look at visualizations of sensor measurements and start time estimates using interactive plots made with PlotLy. The purpose is to dive into interesting days and investigate the start time estimates in more detail.

In [1]:
import sys
sys.path.append("../..")

from src.db.core import db
from src.start_time_detection.tasks import _load_sensor_values
from src.db.common_queries import time_zone_for_building
from src.db.cortex_models import building_sensor_configs
from src.utils import current_utc_time

# Standard data science libraries
import pandas as pd
import numpy as np

# Options for pandas
pd.options.display.max_columns = 20

# Display all cell outputs
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from collections import defaultdict

# widgets
from ipywidgets import widgets
from IPython.display import display

# Plotly
from plotly import tools
import plotly.plotly as py
import plotly.graph_objs as go
from datetime import datetime

import pickle 
import re

## Load Comparisons Data

In the next cell, select the start time estimation comparisons to plot. There are a number of estimates in this directory.

In [3]:
all_comparisons = pickle.load(open('edge_15_no_sat.pkl', 'rb'))
estimates = all_comparisons['ESB']

TRAIN_END = current_utc_time() - pd.Timedelta(days = 30)
TRAIN_START = TRAIN_END - pd.Timedelta(days = 366)

TEST_END = current_utc_time()
TEST_START = TRAIN_END

This cell creates a mapping from building id to building name and vice versa. This can be very helpful for those of us who don't have the buildings memorized!

In [4]:
building_df = pd.read_sql_query("SELECT id, name FROM buildings WHERE active = True", con = db())
id_to_name = {id_: name for id_, name in zip(building_df['id'], building_df['name'])}
name_to_id = {value: key for key, value in id_to_name.items()}
len(name_to_id)

34

## Loading Data

The following cell creates a method for loading a building's data for a specified period of time and the start time estimates. Both of these dataframes are used for plotting: we need the sensor data itself as well as the estimated start time.

In [5]:
DEFAULT_START_TIME_MEASUREMENT_TYPES = [
    "PowerMeasurement",
    "SteamMeasurement",
    "SupplyAirTemperatureMeasurement",
    "StaticPressureMeasurement",
]


def sensors_to_use(building_id, sensor_types=DEFAULT_START_TIME_MEASUREMENT_TYPES):
    """Find building sensors to use. Default measurement types are
       set if not specified"""

    # Find the sensors for the building corresponding to the measurement types
    return (
        db()
        .execute(
            building_sensor_configs.select()
            .where(building_sensor_configs.c.building_id == building_id)
            .where(building_sensor_configs.c.ignore == False)
            .where(building_sensor_configs.c.measurement_type.in_(sensor_types))
        )
        .fetchall()
    )


def data_for_fitting(building_id, start_time, end_time, sensor_types=None):
    """Retrieve data for fitting a model"""
    # Find building sensors to use
    sensors = sensors_to_use(building_id, sensor_types)

    # Get the data
    values = list(
        map(lambda sensor: _load_sensor_values(sensor, start_time, end_time), sensors)
    )

    # Construct configs
    configs = [
        {
            "sensor_id": sensor.id,
            "edge_type": sensor.edge_type,
            "sigma": sensor.sigma,
            "measurement_type": sensor.measurement_type,
        }
        for sensor in sensors
    ]

    return values, configs

def get_dataframe(X, configs):
    """
        Utility function to convert list of lists and
        config file to a dataframe with a multiindex on the columns.
    """
    new_X = []
    idx_to_keep = []

    # Filter out empty measurements
    for i, series in enumerate(X):
        if len(series) > 0:
            idx_to_keep.append(i)
            new_X.append(series)

    df = pd.DataFrame(new_X).transpose()
    # Only retain sensors that did not have an empty measurement
    configs = [conf for i, conf in enumerate(configs) if i in idx_to_keep]
    tuples = list((conf['measurement_type'].split('M')[0], 
                   conf['sensor_id']) for conf in configs) 
    index = pd.MultiIndex.from_tuples(tuples, names = ['type', 'sensor'])
    
    df.columns = index
    df.index = pd.to_datetime(df.index)
    
    return df

def get_building_data(building_id, start_time, end_time, sensor_types=None):
    """Retrieve building data values as a dataframe"""
    
    # Get the values and configuration and convert into a dataframe
    values, configs = data_for_fitting(building_id, start_time, end_time, sensor_types)
    df = get_dataframe(values, configs)
    
    # Remove the time zone information by converting to local time and then removing time zone
    building_tz = time_zone_for_building(building_id)
    df.index = df.index.tz_convert(building_tz).tz_localize(None)
    return df

def get_building_estimates(building_id, all_comparisons):   
    """Retrieve the estimated start times for a building"""
    
    # Make sure to use copy so as not to change the original dataframe
    estimates = all_comparisons[db().execute(f"SELECT name FROM buildings WHERE id = {building_id}").fetchone()[0]].copy()
    
    building_tz = time_zone_for_building(building_id)
    
    # Remove the time zone information by converting to local time (already done) and then removing time zone
    estimates['existing'] = pd.to_datetime(estimates['existing']).dt.tz_localize(None)
    estimates['prediction'] = pd.to_datetime(estimates['prediction']).dt.tz_localize(None)
    
    return estimates

def make_plot_data(building_id, start_time, end_time, sensor_types, comparisons):
    """Get the complete data needed for plotting for a specified period of time"""
    print(f'Fetching data for {id_to_name[building_id]} from {start_time.date()} to {end_time.date()}.')
    data = get_building_data(building_id, start_time, end_time, sensor_types)
    estimates = get_building_estimates(building_id, comparisons)
    return data, estimates 

## Select Building

In the next cell is where you can select the building. You just need to enter a name as a string.

In [6]:
building_name = 'ESB'
building_id = name_to_id[building_name]

The next cell retrieves the data for the building. It gets both the actual sensor measurements and the estimated start times.

In [7]:
df, estimates = make_plot_data(building_id, TEST_START, TEST_END,
                               sensor_types = ['SteamMeasurement', 'PowerMeasurement',
                                               'StaticPressureMeasurement'],
                               comparisons = all_comparisons)
df.head()

Fetching data for ESB from 2018-11-11 to 2018-12-11.


type                StaticPressure                                          \
sensor                       10532     10539     10574     10576     10544   
measured_at                                                                  
2018-11-11 14:00:00      -0.034042  0.006992  0.600263 -0.014885  0.120921   
2018-11-11 14:15:00      -0.034042  0.006992  0.604478 -0.014885  0.120921   
2018-11-11 14:30:00      -0.034042  0.006992  0.600321 -0.014885  0.120921   
2018-11-11 14:45:00      -0.034042  0.006992  0.599693 -0.014885  0.120921   
2018-11-11 15:00:00      -0.034042  0.006992  0.595291 -0.014885  0.120921   

type                                                                   \
sensor                  10543     10546     10540     10541     10548   
measured_at                                                             
2018-11-11 14:00:00 -0.011687  0.001389 -0.038427 -0.002183 -0.058798   
2018-11-11 14:15:00 -0.011687  0.001389 -0.038427 -0.002183 -0.058798   
2018-11-11 14:30:00 -0.011687  0.001389 -0.038427 -0.002183 -0.058798   
2018-11-11 14:45:00 -0.011687  0.001389 -0.038427 -0.002183 -0.058798   
2018-11-11 15:00:00 -0.011687  0.001389 -0.038427 -0.002183 -0.058798   

type                   ...                                             \
sensor                 ...        10648     10580     10593     10655   
measured_at            ...                                              
2018-11-11 14:00:00    ...    -0.012505  0.067851  0.069294 -0.023786   
2018-11-11 14:15:00    ...    -0.012505  0.067851  0.069294 -0.023786   
2018-11-11 14:30:00    ...    -0.012505  0.067851  0.069294 -0.023786   
2018-11-11 14:45:00    ...    -0.012505  0.067851  0.069294 -0.023786   
2018-11-11 15:00:00    ...    -0.012505  0.067851  0.069294 -0.023786   

type                                                                   \
sensor                  10688     10536     10619     10573     10656   
measured_at                                                             
2018-11-11 14:00:00 -0.023954 -0.002844 -0.027821 -0.039479 -0.088567   
2018-11-11 14:15:00 -0.023954 -0.002844 -0.027821 -0.039479 -0.088567   
2018-11-11 14:30:00 -0.023954 -0.002844 -0.027821 -0.039479 -0.088567   
2018-11-11 14:45:00 -0.023954 -0.002844 -0.027821 -0.039479 -0.088567   
2018-11-11 15:00:00 -0.023954 -0.002844 -0.027821 -0.039479 -0.088567   

type                           
sensor                  10557  
measured_at                    
2018-11-11 14:00:00 -0.032611  
2018-11-11 14:15:00 -0.032611  
2018-11-11 14:30:00 -0.032611  
2018-11-11 14:45:00 -0.032611  
2018-11-11 15:00:00 -0.032611  

[5 rows x 174 columns]

In [8]:
df.tail()
estimates.head()

type                StaticPressure                                      \
sensor                       10532     10539     10574 10576     10544   
measured_at                                                              
2018-12-11 12:45:00       0.608770  0.598410  0.447532   NaN  0.599482   
2018-12-11 13:00:00       0.601688  0.597999  0.459940   NaN  0.599482   
2018-12-11 13:15:00       0.597169  0.597999  0.445559   NaN  0.595068   
2018-12-11 13:30:00       0.602881  0.601046  0.468827   NaN  0.597087   
2018-12-11 13:45:00       0.592567  0.600605  0.491357   NaN  0.597087   

type                                                                   \
sensor                  10543     10546     10540     10541     10548   
measured_at                                                             
2018-12-11 12:45:00  0.597070  0.600816  0.598573  0.681469  0.594890   
2018-12-11 13:00:00  0.596969  0.600816  0.598573  0.688836  0.601753   
2018-12-11 13:15:00  0.602475  0.600816  0.598573  0.686761  0.595757   
2018-12-11 13:30:00  0.598302  0.600816  0.598573  0.691894  0.594918   
2018-12-11 13:45:00  0.604352  0.600816  0.598573  0.679238  0.598680   

type                   ...                                            \
sensor                 ...        10648     10580     10593    10655   
measured_at            ...                                             
2018-12-11 12:45:00    ...     0.601576  0.503699  0.601567  0.60034   
2018-12-11 13:00:00    ...     0.599433  0.503699  0.601567  0.60034   
2018-12-11 13:15:00    ...     0.599433  0.503699  0.601567  0.60034   
2018-12-11 13:30:00    ...     0.599433  0.503699  0.601567  0.60034   
2018-12-11 13:45:00    ...     0.599433  0.503699  0.601567  0.60034   

type                                                                   \
sensor                  10688     10536     10619     10573     10656   
measured_at                                                             
2018-12-11 12:45:00  0.598858  0.595773  0.601249  0.599237  0.600677   
2018-12-11 13:00:00  0.598858  0.601449  0.601249  0.599237  0.593221   
2018-12-11 13:15:00  0.598858  0.598398  0.601249  0.599237  0.600731   
2018-12-11 13:30:00  0.598858  0.605578  0.601249  0.599237  0.600731   
2018-12-11 13:45:00  0.598858  0.600188  0.597324  0.599237  0.596778   

type                           
sensor                  10557  
measured_at                    
2018-12-11 12:45:00  0.600731  
2018-12-11 13:00:00  0.600731  
2018-12-11 13:15:00  0.600731  
2018-12-11 13:30:00  0.600731  
2018-12-11 13:45:00  0.600731  

[5 rows x 174 columns]

date existing_formatted prediction_formatted  \
0 2018-11-11                NaT                  NaT   
1 2018-11-12                NaT             06:15 AM   
2 2018-11-13           06:00 AM             06:15 AM   
3 2018-11-14           06:00 AM             06:00 AM   
4 2018-11-15           06:30 AM             06:45 AM   

                      times  \
0                       NaN   
1  [6:20, 6:30, 6:40, 4:15]   
2  [4:15, 6:20, 6:30, 6:40]   
3  [4:15, 6:25, 6:35, 6:45]   
4  [4:30, 6:55, 7:05, 7:15]   

                                 message_description            existing  \
0                                                NaN                 NaT   
1  Cortex must track this day as a holiday as it ...                 NaT   
2  Have chillers on all zones for start up with s... 2018-11-13 06:00:00   
3  Start steam at 4:15, have chiller 6 on setpoin... 2018-11-14 06:00:00   
4  Start steam at 4:30 AM, have chiller 6 on setp... 2018-11-15 06:30:00   

           prediction  
0                 NaT  
1 2018-11-12 06:15:00  
2 2018-11-13 06:15:00  
3 2018-11-14 06:00:00  
4 2018-11-15 06:45:00

The next cell is a utility function used for formatting a time.

In [9]:
def format_time(dt):
    if pd.isnull(dt):
        return "NaT"
    else:
        return datetime.strftime(dt, "%H:%M %p")
    
format_time(datetime.now())

'13:55 PM'

# Start Time Plot

The next cell forms the heart of the visualization. This takes in a dataframe of building sensor measurements, and the start time estimates for the building. It then shows the sensor data and the estimates on the plot. We can see both the original estimates (using a window of 30 minutes and the selected sensors for the building or the default sensors if none are specified) and the new estimates from whatever configuration was used in to generate the new estimates. 

The plot can then be generated and explored. It's not that robust yet, but good as a proof of concept.

In [10]:
class StartTimePlot:
    """Make a start time plot with estimated start times"""
    
    def __init__(self, building_name, data, estimates):
        """
        :param building_name: string for the building name
        :param data: a dataframe with the index as the time
        :param estimates: a dataframe of estimated start times
        
        """
        self.building_name = building_name
        self.data = data
        self.estimates = estimates
        
        # Enforce date times
        self.data.index = pd.to_datetime(self.data.index)
        self.estimates['date'] = pd.to_datetime(self.estimates['date'])
        self.estimates['existing'] = pd.to_datetime(self.estimates['existing'])
        self.estimates['prediction'] = pd.to_datetime(self.estimates['prediction'])
    
    def format_data(self, date):
        """
        Format data for plotly

        :param date: String representing the date to plot
        
        :return traces: a list of plotly traces

        """
        datetime = pd.to_datetime(date)
        date = datetime.date()
        
        # Don't modify originals
        df = self.data.copy()
        est = self.estimates.copy()
        
        # Subset to the correct day
        df = df.loc[df.index.date == date].copy()

        # Estimates
        est = est.loc[est['date'].dt.date == date].copy()

        existing = pd.NaT
        prediction = pd.NaT
        # See if there is an estimate and prediction on this date
        try:
            existing = est['existing'].values[0].copy()
            prediction = est['prediction'].values[0].copy()

            existing = pd.to_datetime(est['existing'].values[0])
            prediction = pd.to_datetime(est['prediction'].values[0])
        except:
            pass

        traces = defaultdict(list)

        # Sensor types
        stypes = list(df.columns.levels[0])

        # Keep track of mins and maxes for plotting lines
        maxes = {stype: -np.inf for stype in stypes}
        mins = {stype: np.inf for stype in stypes}

        # Iterate through the sensors in the dataframe
        for c in df:

            stype = c[0]

            # Find the minimum and maximum value
            max_value = df.loc[:, (stype, c)].max()[0]
            min_value = df.loc[:, (stype, c)].min()[0]
            if max_value > maxes[stype]:
                maxes[stype] = max_value
            if min_value < mins[stype]:
                mins[stype] = min_value

            # Add the data from the sensor
            traces[stype].append(go.Scatter(x = df.index,
                                   y = df[c], hoverinfo = 'none',
                                   showlegend = False))

        # Add the vertical lines at the estimates
        if (not pd.isnull(existing)) and (not pd.isnull(prediction)):
            
            for i, stype in enumerate(stypes):
                min_ = mins[stype] - 0.05 * mins[stype]
                max_ = maxes[stype] + 0.05 * maxes[stype]
                
                traces[stype].append(go.Scatter(x = [existing, existing],
                                     y = [min_, max_],
                                     line = dict(
                                            color = 'black',
                                            width = 4,
                                            dash = 'dashdot'),
                                     mode = 'lines',
                                     text = f'original: {format_time(existing)}',
                                     name = 'original',
                                     opacity = 1,
                                     hoverinfo = 'text',
                                     showlegend = True if i == 0 else False))
                traces[stype].append(go.Scatter(x = [prediction, prediction],
                                     y = [min_, max_],
                                     line = dict(
                                            color = 'red',
                                            width = 4,
                                            dash = 'dashdot'),
                                     mode = 'lines',
                                     text = f'prediction: {format_time(prediction)}',
                                     name = 'prediction',
                                     opacity = 1,
                                     hoverinfo = 'text',
                                     showlegend = True if i == 0 else False))
        else:
            for stype in stypes:
                for _ in range(2):
                    traces[stype].append(go.Scatter(x = [datetime, datetime], y = [0, 0], 
                                                    opacity=0, showlegend = False))
                
        return traces
    
    
    def update_data(self, value):
        """
        Update the day shown on the plot
        
        :param label: the label attribute of the widgets selection
        
        :return: updates the plotted data
        """
        
        # Get the new traces
        traces = self.format_data(value['new'])

        stypes = list(traces.keys())

        # Each sensor type gets a new row
        rows = len(stypes)

        # Make the basic figure
        fig = tools.make_subplots(rows = rows, cols = 1, print_grid = False,
                                  subplot_titles = [f'{t}' for t in stypes]);

        # Iterate through the sensor types
        for i, stype in enumerate(stypes):
            
            # Iterate through the sensors 
            for trace in traces[stype]:
                fig.append_trace(trace, i + 1, 1)

        self.fw.update(data = fig.data)
        self.fw.layout.update(title = f'{self.building_name}: {str(value["new"])}')
                              
        
    def make_plot(self, date):
        """
        Generate the plot for a particular day
        
        :param date: string representing the day
        
        :return wbox: a widget with the selection tool and plot
        
        """
        
        self.w = widgets.DatePicker(
                    description = 'Date')
    
        self.w.observe(handler = self.update_data, names = 'value')
        
        traces = self.format_data(date)
        stypes = list(traces.keys())

        # Each sensor type gets a new row
        rows = len(stypes)

        # Make the basic figure
        fig = tools.make_subplots(rows = rows, cols = 1, print_grid = False,
                                  subplot_titles = [f'{t}' for t in stypes])
        fig.layout['title'] = f'{self.building_name}: {date}'
        fig.layout['height'] = rows * 500
        fig.layout['width'] = 950
        fig.layout['font']= dict(size=20, color='black')
                              
        # Iterate through the sensor types
        for i, stype in enumerate(stypes):
            
            # Iterate through the sensors 
            for trace in traces[stype]:
                fig.append_trace(trace, i + 1, 1)
                              
            fig.layout['annotations'][i]['font']['size'] = 16
                
        self.fw = go.FigureWidget(data = fig.data, layout = fig.layout)
        wbox = widgets.VBox([self.w, self.fw])
        
        return wbox

                              
    def display_plot(self, plot):
        display(plot)

In [11]:
st = StartTimePlot(building_name, df, estimates)
plot = st.make_plot('2018-12-10')
st.display_plot(plot)

    'data': [{'hoverinfo': 'none',
 …

# Conclusions

We are back to the beginning! We are going to have to tweak sensors used for individual buildings. 